# How to Fine-Tune Large Language Models (LLMs) with Hugging Face in 2024

Large Language Models (LLMs) have seen significant progress over the last year. We have transitioned from having no direct competitors to ChatGPT to a diverse array of LLMs, including Meta AI's Llama 2, Mistral's Mistral & Mixtral models, TII Falcon, and many more. These LLMs can be employed for a variety of tasks, such as chatbots, question answering, and summarization without requiring additional training. However, if you want to customize a model for your specific application, you may need to fine-tune the model on your data to achieve higher quality results than simple prompting, or to save costs by training smaller, more efficient models.

These are the steps I followed to fine-tune open LLMs using Hugging Face TRL, Transformers, and datasets. We will cover the following:

1.   Define our use case
2.   Set up the development environment
3.   Create and prepare the dataset
4.   Fine-tune the LLM using **trl** and the **SFTTrainer**
5.   Test and evaluate the LLM
6.   Deploy the model to Hugging Face space


Note: For this project, I used Google's Colab A100 GPU. The instructions can be easily adapted to run on larger GPUs.

## 1. Define our use case

The goal is to fine-tune an open Large Language Model (LLM) using a dataset containing extensive database materials, including SQL scripts, documentation, and query examples. The resulting model should be capable of answering a wide range of database-related questions, assisting with database management, optimizing SQL queries, and providing insights into database design and maintenance.

## 2. Set up the development environment


In this section, we are installing the necessary libraries and tools required for fine-tuning a Large Language Model (LLM) using Hugging Face's ecosystem.



*   **torch==2.1.2**: Installs PyTorch version 2.1.2, a powerful deep learning framework that provides tensor computation and automatic differentiation.
*   **tensorboard**: Installs TensorBoard, a tool for visualizing metrics such as loss and accuracy during model training.
*   **transformers==4.36.2**: Installs the Transformers library version 4.36.2, which provides state-of-the-art pre-trained models and tools for natural language processing.
*   **datasets==2.16.1**: Installs the Datasets library version 2.16.1, used for accessing and managing large datasets efficiently.
*   **accelerate==0.26.1**: Installs the Accelerate library version 0.26.1, which helps in making distributed training easier and more efficient.
*   **evaluate==0.4.1**: Installs the Evaluate library version 0.4.1, used for evaluating machine learning models.
*   **bitsandbytes==0.42.0**: Installs the BitsandBytes library version 0.42.0, which optimizes memory usage and speeds up training on GPUs.
*   **trl**: Installs the TRL (Transformers Reinforcement Learning) library from Hugging Face's GitHub repository. This library provides tools and techniques for fine-tuning LLMs using reinforcement learning.
*   **peft**: Installs the PEFT (Parameter-Efficient Fine-Tuning) library from Hugging Face's GitHub repository. This library helps in fine-tuning models more efficiently by updating only a subset of the model parameters.

By executing these commands, we set up our environment with the necessary libraries for fine-tuning LLMs, ensuring we have the latest tools and frameworks to work with.



In [ ]:
# Install Pytorch & other libraries
!pip install "torch==2.1.2" tensorboard

# Install Hugging Face libraries
!pip install  --upgrade \
  "transformers==4.36.2" \
  "datasets==2.16.1" \
  "accelerate==0.26.1" \
  "evaluate==0.4.1" \
  "bitsandbytes==0.42.0" \
  # "trl==0.7.10" # \
  # "peft==0.7.1" \

# install peft & trl from github
!pip install git+https://github.com/huggingface/trl@a3c5b7178ac4f65569975efadc97db2f3749c65e --upgrade
!pip install git+https://github.com/huggingface/peft@4a1559582281fc3c9283892caea8ccef1d6f5a4f --upgrade

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 670.2/670.2 MB 1.8 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 209.8/209.8 MB 8.2 MB/s eta 0:00:00
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-man

If you're using a GPU with Ampere architecture (e.g., NVIDIA A10G or RTX 4090/3090) or newer, you can leverage Flash Attention. This method reorders attention computation and uses classical techniques like tiling and recomputation to significantly speed up training (up to 3x faster) and reduce memory usage from quadratic to linear in sequence length. For more details, visit [FlashAttention](https://github.com/Dao-AILab/flash-attention/tree/main).

Note: If your machine has less than 96GB of RAM and many CPU cores, reduce the number of MAX_JOBS. For example, on a g5.2xlarge instance, we used 4.

In [ ]:
import torch; assert torch.cuda.get_device_capability()[0] >= 8, 'Hardware not supported for Flash Attention'
# install flash-attn
!pip install ninja packaging
!MAX_JOBS=4 pip install flash-attn --no-build-isolation

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.2/307.2 kB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 41.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.2/43.2 kB 5.7 MB/s eta 0:00:00
  Created wheel for flash-attn: filename=flash_attn-2.5.9.post1-cp310-cp310-linux_x86_64.whl size=120585039 sha256=932debba074293888ea81ee11f111f2b9f9183da0e0bbea45a48b260d2231b41
  Stored in directory: /root/.cache/pip/wheels/cc/ad/f6/7ccf0238790d6346e9fe622923a76ec218e890d356b9a2754a
Successfully built flash-attn


Installing Flash Attention can take 10-45 minutes.

We will use the Hugging Face Hub for remote model versioning, which involves automatically pushing our model, logs, and information to the Hub during training. You need to register on Hugging Face, create a token with write permission when ran, the `notebook_login` utility from the `huggingface_hub` will ask for the token you generated previously enter it and press login.








In [ ]:
from huggingface_hub import notebook_login

notebook_login()

## 3. Create and prepare the dataset


Once you've determined that fine-tuning is the right solution, you need to create a dataset. This dataset should contain diverse examples of the task you want to solve. You can create a dataset in several ways:

* Using existing open-source datasets (e.g., Spider)
* Using LLMs to create synthetic datasets (e.g., Alpaca)
* Using humans to create datasets (e.g., Dolly)
* Using a combination of methods (e.g., Orca)

Each method has its pros and cons, depending on budget, time, and quality requirements. For instance, existing datasets are easy to use but may not be tailored to your specific needs, while human-created datasets are accurate but can be costly and time-consuming. Combining methods, as shown in Orca, can balance these factors.

We will use my public dataset called [stefutz101/db_course-synthetic_text_to_sql_dataset](https://huggingface.co/datasets/stefutz101/db_course-synthetic_text_to_sql_dataset), which includes natural language instructions, schema definitions, corresponding SQL queries and different questions and answers about DBMS.

With the latest release of `trl`, we support popular instruction and conversation dataset formats. You just need to convert your dataset to one of these supported formats, and `trl` will handle the rest.

* conversational format
```
{"messages": [{"role": "system", "content": "You are..."}, {"role": "user", "content": "..."}, {"role": "assistant", "content": "..."}]}
{"messages": [{"role": "system", "content": "You are..."}, {"role": "user", "content": "..."}, {"role": "assistant", "content": "..."}]}
{"messages": [{"role": "system", "content": "You are..."}, {"role": "user", "content": "..."}, {"role": "assistant", "content": "..."}]}
```

* instruction format
```
{"prompt": "<prompt text>", "completion": "<ideal generated text>"}
{"prompt": "<prompt text>", "completion": "<ideal generated text>"}
{"prompt": "<prompt text>", "completion": "<ideal generated text>"}
```

We'll use a generated dataset called [stefutz101/db_course-synthetic_text_to_sql_dataset](https://huggingface.co/datasets/stefutz101/db_course-synthetic_text_to_sql_dataset) from the 🤗 Datasets library. We will convert it into a conversational format by including the schema definition in the system message for our assistant. We'll then save the dataset as a JSONL file for fine-tuning our model we will use 9501 entries for training and 500 entries for testing.


In [ ]:
from datasets import load_dataset

# Convert dataset to OAI messages
system_message = """You are an virtual assistent that will answer to the students and their questions about Database 1 module. The Stundets will ask you questions in English and you will answer to their questions based on the provided SCHEMA.
SCHEMA:
{schema}"""

def create_conversation(sample):
  if sample["instruction"] is None or sample["instruction"] or sample["instruction"]:
    print(sample)
  return {
    "messages": [
      {"role": "system", "content": system_message.format(schema=sample["instruction"])},
      {"role": "user", "content": sample["input"]},
      {"role": "assistant", "content": sample["output"]}
    ]
  }

# Load dataset from the hub
dataset = load_dataset("stefutz101/db_course-synthetic_text_to_sql_dataset", split="train")
dataset = dataset.shuffle()

# Convert dataset to OAI messages
dataset = dataset.map(create_conversation, remove_columns=dataset.features, batched=False)
# split dataset into 9,501 training samples and 500 test samples
dataset = dataset.train_test_split(test_size=500/9501)

print(dataset["train"][345]["messages"])

# save datasets to disk
dataset["train"].to_json("train_dataset.json", orient="records")
dataset["test"].to_json("test_dataset.json", orient="records")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Generating train split: 0 examples [00:00, ? examples/s]

Map:   0%|          | 0/10001 [00:00<?, ? examples/s]

{'output': "This SQL query identifies the top 3 donors in the 'Education' category in H2 2020 by joining the 'donors' and 'donations' tables, summing the 'amount' column for each donor, and filtering based on the specified date range and category. The results are then grouped by donor name, sorted in descending order by the total donation amount, and limited to the top 3 records. SELECT d.name, SUM(donations.amount) as total_donations FROM donations JOIN donors ON donations.donor_id = donors.id WHERE donations.donation_date BETWEEN '2020-07-01' AND '2020-12-31' AND donors.category = 'Education' GROUP BY d.name ORDER BY total_donations DESC LIMIT 3;", 'instruction': "CREATE TABLE donors (id INT, name VARCHAR(50), category VARCHAR(20)); INSERT INTO donors (id, name, category) VALUES (1, 'John Doe', 'Education'), (2, 'Jane Smith', 'Health'), (3, 'Bob Johnson', 'Education'), (4, 'Alice Williams', 'Arts & Culture'); CREATE TABLE donations (id INT, donor_id INT, amount DECIMAL(10,2), donatio

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




{'output': 'The key structural rules mentioned in the text chunk are information representation and view updating.', 'instruction': 'Provide an answer to the following question:', 'input': 'What are the key structural rules mentioned in the text chunk?'}
{'output': "This query calculates the percentage of companies founded by individuals with disabilities in the cybersecurity sector. It does so by using a subquery to calculate the total number of companies and then dividing the count of companies founded by individuals with disabilities in the cybersecurity sector by the total number of companies and multiplying by 100.0. SELECT (COUNT(*) * 100.0 / (SELECT COUNT(*) FROM company)) AS percentage FROM company WHERE company.founder_identity = 'Individual with a disability' AND company.industry = 'Cybersecurity';", 'instruction': 'CREATE TABLE company (id INT, name TEXT, industry TEXT, founding_date DATE, founder_identity TEXT);', 'input': 'What is the percentage of companies founded by in

Creating json from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Creating json from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

465777

## 4. Fine-tune LLM using `trl` and the `SFTTrainer`

We are now ready to fine-tune our model using the SFTTrainer from trl. The SFTTrainer, a subclass of the Trainer from the transformers library, simplifies the process of supervising fine-tuning open LLMs. It supports logging, evaluation, and checkpointing while adding additional features such as:

* Dataset formatting for conversational and instruction formats
* Training on completions only, ignoring prompts
* Packing datasets for more efficient training
* PEFT (parameter-efficient fine-tuning) support, including Q-LoRA
* Preparing the model and tokenizer for conversational fine-tuning (e.g., adding special tokens)

We will use dataset formatting, packing, and PEFT features. We will use QLoRA, a method to reduce the memory footprint of large language models during fine-tuning without sacrificing performance by using quantization. For more details, check out the blog post on QLoRA.

Let's get started by loading our JSON dataset from the disk. 🚀

In [ ]:
from datasets import load_dataset

# Load jsonl data from disk
dataset = load_dataset("json", data_files="train_dataset.json", split="train")

Generating train split: 0 examples [00:00, ? examples/s]

Next, we will load our LLM, specifically CodeLlama 7B, designed for general code synthesis and understanding. You can easily swap it for another model like Mistral, Mixtral, or TII Falcon by changing the `model_id` variable. We will use bitsandbytes to quantize the model to 4-bit.

**Note:** Larger models require more memory. The 7B version can be tuned on 24GB GPUs. If you have a smaller GPU, consider using a smaller model.

Properly preparing the model and tokenizer for training chat/conversational models is crucial. We need to add new special tokens to the tokenizer and model to teach them the different roles in a conversation. The `setup_chat_format` method in `trl` helps with this by:

* Adding special tokens to the tokenizer to indicate the start and end of a conversation.
* Resizing the model’s embedding layer to accommodate the new tokens.
* Setting the chat_template of the tokenizer to format input data into a chat-like format, with the default being chatml from OpenAI.

In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig
from trl import setup_chat_format

# Hugging Face model id
model_id = "codellama/CodeLlama-7b-hf" # or `mistralai/Mistral-7B-v0.1`

# BitsAndBytesConfig int-4 config
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True, bnb_4bit_use_double_quant=True, bnb_4bit_quant_type="nf4", bnb_4bit_compute_dtype=torch.bfloat16
)

# Load model and tokenizer
model = AutoModelForCausalLM.from_pretrained(
    model_id,
    device_map="auto",
    attn_implementation="flash_attention_2",
    torch_dtype=torch.bfloat16,
    quantization_config=bnb_config
)
tokenizer = AutoTokenizer.from_pretrained(model_id)
tokenizer.padding_side = 'right' # to prevent warnings

# # set chat template to OAI chatML, remove if you start from a fine-tuned model
model, tokenizer = setup_chat_format(model, tokenizer)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


config.json:   0%|          | 0.00/637 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/25.1k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/9.98G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/3.50G [00:00<?, ?B/s]

...

generation_config.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/749 [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/411 [00:00<?, ?B/s]

The `SFTTrainer` supports a native integration with `peft`, making it easy to efficiently fine-tune LLMs using methods like QLoRA. We just need to create a `LoraConfig` and provide it to the trainer. Our `LoraConfig` parameters are defined based on the [QLoRA paper](https://arxiv.org/pdf/2305.14314.pdf) and Sebastian's [blog post](https://magazine.sebastianraschka.com/p/practical-tips-for-finetuning-llms).

In [ ]:
from peft import LoraConfig

# LoRA config based on QLoRA paper & Sebastian Raschka experiment
peft_config = LoraConfig(
        lora_alpha=128,
        lora_dropout=0.05,
        r=256,
        bias="none",
        target_modules="all-linear",
        task_type="CAUSAL_LM",
)

Before we can start our training we need to define the hyperparameters (`TrainingArguments`) we want to use.

In [ ]:
from transformers import TrainingArguments

args = TrainingArguments(
    output_dir="code-llama-7b-databases-finetuned2", # directory to save and repository id
    num_train_epochs=3,                     # number of training epochs
    per_device_train_batch_size=3,          # batch size per device during training
    gradient_accumulation_steps=2,          # number of steps before performing a backward/update pass
    gradient_checkpointing=True,            # use gradient checkpointing to save memory
    optim="adamw_torch_fused",              # use fused adamw optimizer
    logging_steps=10,                       # log every 10 steps
    save_strategy="epoch",                  # save checkpoint every epoch
    learning_rate=2e-4,                     # learning rate, based on QLoRA paper
    bf16=True,                              # use bfloat16 precision
    tf32=True,                              # use tf32 precision
    max_grad_norm=0.3,                      # max gradient norm based on QLoRA paper
    warmup_ratio=0.03,                      # warmup ratio based on QLoRA paper
    lr_scheduler_type="constant",           # use constant learning rate scheduler
    push_to_hub=True,                       # push model to hub
    report_to="tensorboard",                # report metrics to tensorboard
)

We now have every building block to create our `SFTTrainer` and start training our model.

In [ ]:
from trl import SFTTrainer

max_seq_length = 3072 # max sequence length for model and packing of the dataset

trainer = SFTTrainer(
    model=model,
    args=args,
    train_dataset=dataset,
    peft_config=peft_config,
    max_seq_length=max_seq_length,
    tokenizer=tokenizer,
    packing=True,
    dataset_kwargs={
        "add_special_tokens": False,  # We template with special tokens
        "append_concat_token": False, # No need to add additional separator token
    }
)

Generating train split: 0 examples [00:00, ? examples/s]

We can start training our model by calling the `train()` method on our `Trainer` instance. This will start the training loop and train our model for 3 epochs. Since we are using a PEFT method, we will only save the adapted model weights and not the full model.

In [ ]:
# start training, the model will be automatically saved to the hub and the output directory
trainer.train()

# save model
trainer.save_model()

You're using a CodeLlamaTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.
`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`...
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:429: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
The input hidden states seems to be silently casted in float32, this might be related to the fact you have upcasted embedding or layer norm layers in float32. We will cast back the input in torch.bfloat16.


/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:141: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:429: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/utils/save_a

AttributeError: 'SFTTrainer' object has no attribute 'save_pretrained'

The training with Flash Attention for 3 epochs with a dataset of 9.5k samples took 00:45:58 on a `A100 GPU`. The instance costs `11.34 points/h` which brings us to a total cost of only 1.8$.

## Merge LoRA adapter in to the original model

When using QLoRA, only the adapters are trained, so only the adapter weights are saved during training, not the full model. To save the full model for easier use with Text Generation Inference, you can merge the adapter weights into the model weights using the `merge_and_unload` method, and then save the complete model with the `save_pretrained` method. This will produce a default model suitable for inference. Then we weill use `push_to_hub` method to push both `merged_model` and the `tokenizer`.

**Note**: This process might require more than 30GB of CPU memory.

In [ ]:
### COMMENT IN TO MERGE PEFT AND BASE MODEL ####
from peft import AutoPeftModelForCausalLM

# Load PEFT model on CPU
model = AutoPeftModelForCausalLM.from_pretrained(
    args.output_dir,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True,
)
# Merge LoRA and base model and save
merged_model = model.merge_and_unload()
merged_model.save_pretrained(args.output_dir,safe_serialization=True, max_shard_size="2GB")
# save model
merged_model.push_to_hub("stefutz101/code-llama-7b-databases-finetuned2")
tokenizer.push_to_hub("stefutz101/code-llama-7b-databases-finetuned2")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Upload 3 LFS files:   0%|          | 0/3 [00:00<?, ?it/s]

model-00002-of-00003.safetensors:   0%|          | 0.00/4.95G [00:00<?, ?B/s]

model-00001-of-00003.safetensors:   0%|          | 0.00/4.94G [00:00<?, ?B/s]

model-00003-of-00003.safetensors:   0%|          | 0.00/3.59G [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/stefutz101/code-llama-7b-databases-finetuned2/commit/a7d5136d254ac8a18401a198af7ff10fb98bb58a', commit_message='Upload tokenizer', commit_description='', oid='a7d5136d254ac8a18401a198af7ff10fb98bb58a', pr_url=None, pr_revision=None, pr_num=None)

## 5. Test and evaluate the LLM

After training, we will evaluate and test our model by loading different samples from the original dataset and using a simple loop to measure accuracy.

**Note**: *Evaluating generative AI models is complex because a single input can have multiple correct outputs. For more information on evaluating generative models, refer to the blog post [Evaluate LLMs and RAG: A Practical Example Using Langchain and Hugging Face.](https://www.philschmid.de/evaluate-llm)*

In [ ]:
import torch
from peft import AutoPeftModelForCausalLM
from transformers import AutoTokenizer, pipeline

peft_model_id = "./code-llama-7b-databases-finetuned2"
# peft_model_id = args.output_dir

# Load Model with PEFT adapter
model = AutoPeftModelForCausalLM.from_pretrained(
  peft_model_id,
  device_map="auto",
  torch_dtype=torch.float16
)
tokenizer = AutoTokenizer.from_pretrained(peft_model_id)
# load into pipeline
pipe = pipeline("text-generation", model=model, tokenizer=tokenizer)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
The model 'PeftModelForCausalLM' is not supported for text-generation. Supported models are ['BartForCausalLM', 'BertLMHeadModel', 'BertGenerationDecoder', 'BigBirdForCausalLM', 'BigBirdPegasusForCausalLM', 'BioGptForCausalLM', 'BlenderbotForCausalLM', 'BlenderbotSmallForCausalLM', 'BloomForCausalLM', 'CamembertForCausalLM', 'LlamaForCausalLM', 'CodeGenForCausalLM', 'CpmAntForCausalLM', 'CTRLLMHeadModel', 'Data2VecTextForCausalLM', 'ElectraForCausalLM', 'ErnieForCausalLM', 'FalconForCausalLM', 'FuyuForCausalLM', 'GitForCausalLM', 'GPT2LMHeadModel', 'GPT2LMHeadModel', 'GPTBigCodeForCausalLM', 'GPTNeoForCausalLM', 'GPTNeoXForCausalLM', 'GPTNeoXJapaneseForCausalLM', 'GPTJForCausalLM', 'LlamaForCausalLM', 'MarianForCausalLM', 'MBartForCausalLM', 'MegaForCaus

Let’s load our test dataset try to generate an instruction.

In [ ]:
from datasets import load_dataset
from random import randint


# Load our test dataset
eval_dataset = load_dataset("json", data_files="test_dataset.json", split="train")
rand_idx = randint(0, len(eval_dataset))

# Test on sample
prompt = pipe.tokenizer.apply_chat_template(eval_dataset[rand_idx]["messages"][:2], tokenize=False, add_generation_prompt=True)
outputs = pipe(prompt, max_new_tokens=256, do_sample=False, temperature=0.1, top_k=50, top_p=0.1, eos_token_id=pipe.tokenizer.eos_token_id, pad_token_id=pipe.tokenizer.pad_token_id)

print(f"Query:\n{eval_dataset[rand_idx]['messages'][1]['content']}")
print(f"Original Answer:\n{eval_dataset[rand_idx]['messages'][2]['content']}")
print(f"Generated Answer:\n{outputs[0]['generated_text'][len(prompt):].strip()}")

Generating train split: 0 examples [00:00, ? examples/s]

/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:394: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(


Query:
How is schema modification achieved in SQL?
Original Answer:
Schema modification in SQL is achieved through commands like ALTER TABLE, which allows changes to a table's schema by adding or removing columns and applying constraints.
Generated Answer:
Schema modification in SQL is achieved through commands like ALTER TABLE, which allows changes to a table's schema by adding or removing columns and applying constraints.


In [ ]:
from datasets import load_dataset
from random import randint


# Load our test dataset
eval_dataset = load_dataset("json", data_files="test_dataset.json", split="train")
rand_idx = randint(0, len(eval_dataset))

# Test on sample
prompt = pipe.tokenizer.apply_chat_template(eval_dataset[rand_idx]["messages"][:2], tokenize=False, add_generation_prompt=True)
outputs = pipe(prompt, max_new_tokens=256, do_sample=False, temperature=0.1, top_k=50, top_p=0.1, eos_token_id=pipe.tokenizer.eos_token_id, pad_token_id=pipe.tokenizer.pad_token_id)

print(f"Query:\n{eval_dataset[rand_idx]['messages'][1]['content']}")
print(f"Original Answer:\n{eval_dataset[rand_idx]['messages'][2]['content']}")
print(f"Generated Answer:\n{outputs[0]['generated_text'][len(prompt):].strip()}")

/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:394: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(


Query:
Which broadband subscribers in the Southeast region have had the most usage in the past year?
Original Answer:
This query identifies the broadband subscriber in the Southeast region who has had the most usage in the past year by joining the 'subscribers' and 'usage' tables on the 'id' column. It then filters for subscribers in the Southeast region and those who have usage records in the past year. It calculates the sum of the 'data_usage' column for each subscriber and orders the results in descending order. It finally returns the 'id' of the subscriber with the highest total usage. SELECT subscribers.id, SUM(usage.data_usage) as total_usage FROM subscribers JOIN usage ON subscribers.id = usage.subscriber_id WHERE subscribers.region = 'Southeast' AND usage.usage_date >= DATE_SUB(CURRENT_DATE, INTERVAL 1 YEAR) GROUP BY subscribers.id ORDER BY total_usage DESC LIMIT 1;
Generated Answer:
This query joins the subscribers and usage tables on the subscriber_id column, filters for reco

In [ ]:
from datasets import load_dataset
from random import randint


# Load our test dataset
eval_dataset = load_dataset("json", data_files="test_dataset.json", split="train")
rand_idx = randint(0, len(eval_dataset))

# Test on sample
prompt = pipe.tokenizer.apply_chat_template(eval_dataset[rand_idx]["messages"][:2], tokenize=False, add_generation_prompt=True)
outputs = pipe(prompt, max_new_tokens=256, do_sample=False, temperature=0.1, top_k=50, top_p=0.1, eos_token_id=pipe.tokenizer.eos_token_id, pad_token_id=pipe.tokenizer.pad_token_id)

print(f"Query:\n{eval_dataset[rand_idx]['messages'][1]['content']}")
print(f"Original Answer:\n{eval_dataset[rand_idx]['messages'][2]['content']}")
print(f"Generated Answer:\n{outputs[0]['generated_text'][len(prompt):].strip()}")

Query:
What is data redundancy?
Original Answer:
Data redundancy occurs when the same piece of data exists in multiple places within a database. While it can improve data availability, excessive redundancy can lead to data anomalies and increased storage costs.
Generated Answer:
Data redundancy is the practice of storing the same data in multiple locations or formats to ensure data availability, reliability, or resilience. It can be intentional (e.g., backup copies) or unintentional (e.g., duplicate data entries).


In [ ]:
from datasets import load_dataset
from random import randint


# Load our test dataset
eval_dataset = load_dataset("json", data_files="test_dataset.json", split="train")
rand_idx = randint(0, len(eval_dataset))

# Test on sample
prompt = pipe.tokenizer.apply_chat_template(eval_dataset[rand_idx]["messages"][:2], tokenize=False, add_generation_prompt=True)
outputs = pipe(prompt, max_new_tokens=256, do_sample=False, temperature=0.1, top_k=50, top_p=0.1, eos_token_id=pipe.tokenizer.eos_token_id, pad_token_id=pipe.tokenizer.pad_token_id)

print(f"Query:\n{eval_dataset[rand_idx]['messages'][1]['content']}")
print(f"Original Answer:\n{eval_dataset[rand_idx]['messages'][2]['content']}")
print(f"Generated Answer:\n{outputs[0]['generated_text'][len(prompt):].strip()}")

Query:
List all virtual reality (VR) games and their designers.
Original Answer:
Join the Games and VRGames tables on GameID, then filter for VR games and list their titles and designers. SELECT Games.Title, VRGames.Designer FROM Games INNER JOIN VRGames ON Games.GameID = VRGames.GameID WHERE Games.Platform = 'VR';
Generated Answer:
This query joins the Games and VRGames tables on the GameID column, then returns the title, genre, platform, and designer of all VR games. SELECT g.Title, g.Genre, g.Platform, v.Designer FROM Games g JOIN VRGames v ON g.GameID = v.GameID;


In [ ]:
from datasets import load_dataset
from random import randint


# Load our test dataset
eval_dataset = load_dataset("json", data_files="test_dataset.json", split="train")
rand_idx = randint(0, len(eval_dataset))

# Test on sample
prompt = pipe.tokenizer.apply_chat_template(eval_dataset[rand_idx]["messages"][:2], tokenize=False, add_generation_prompt=True)
outputs = pipe(prompt, max_new_tokens=256, do_sample=False, temperature=0.1, top_k=50, top_p=0.1, eos_token_id=pipe.tokenizer.eos_token_id, pad_token_id=pipe.tokenizer.pad_token_id)

print(f"Query:\n{eval_dataset[rand_idx]['messages'][1]['content']}")
print(f"Original Answer:\n{eval_dataset[rand_idx]['messages'][2]['content']}")
print(f"Generated Answer:\n{outputs[0]['generated_text'][len(prompt):].strip()}")

Query:
Count the number of scandium refineries in Canada and Argentina as of 2021.
Original Answer:
Counts the total number of scandium refineries in Canada and Argentina as of 2021 by summing the 'num_refineries' column values where 'country' is either 'Canada' or 'Argentina'. SELECT SUM(num_refineries) FROM scandium_refineries WHERE country IN ('Canada', 'Argentina');
Generated Answer:
This query counts the number of scandium refineries in Canada and Argentina as of 2021 by selecting the num_refineries column for rows where the country is either Canada or Argentina and the year is 2021. SELECT num_refineries FROM scandium_refineries WHERE country IN ('Canada', 'Argentina') AND year = 2021;


Perfect! Our model successfully generated a SQL query based on the natural language instruction. Next, we will evaluate our model on the full 500 samples of our test dataset.

**Note:** Evaluating generative models is complex. In this example, we used the accuracy of the generated SQL compared to the ground truth SQL as our metric. Alternatively, you could execute the generated SQL query and compare the results with the ground truth, which is more accurate but requires more setup.

In [ ]:
from tqdm import tqdm


def evaluate(sample):
    prompt = pipe.tokenizer.apply_chat_template(sample["messages"][:2], tokenize=False, add_generation_prompt=True)
    outputs = pipe(prompt, max_new_tokens=256, do_sample=True, temperature=0.7, top_k=50, top_p=0.95, eos_token_id=pipe.tokenizer.eos_token_id, pad_token_id=pipe.tokenizer.pad_token_id)
    predicted_answer = outputs[0]['generated_text'][len(prompt):].strip()
    if predicted_answer == sample["messages"][2]["content"]:
        return 1
    else:
        return 0

success_rate = []
number_of_eval_samples = 500
# iterate over eval dataset and predict
for s in tqdm(eval_dataset.shuffle().select(range(number_of_eval_samples))):
    success_rate.append(evaluate(s))

# compute accuracy
accuracy = sum(success_rate)/len(success_rate)

print(f"Accuracy: {accuracy*100:.2f}%")


100%|██████████| 500/500 [37:16<00:00,  4.47s/it]

Accuracy: 14.20%


To evaluate our model, we employ a more nuanced method that compares the semantic similarity between the generated SQL queries and the reference SQL queries. Here's a detailed description of the evaluation process:

1. **Initialize BERT Model and Tokenizer:** We use the BERT model and tokenizer from the 'bert-base-uncased' pre-trained model to compute embeddings for our text data.
2. **Compute Text Embeddings:** A function get_embedding is defined to convert text into embeddings using the BERT model. This function tokenizes the input text, processes it through the BERT model, and computes the mean of the last hidden state to obtain a fixed-size embedding vector.
3. **Generate Predictions and Compute Similarity:** The `evaluate` function generates a SQL query based on a natural language instruction and then computes the semantic similarity between the generated SQL query and the reference SQL query using cosine similarity.
4. **Calculate Success Rate:** We iterate over a subset of the evaluation dataset, generate predictions, and compute the success rate based on the defined similarity threshold.
5. **Print Accuracy:** Finally, we calculate and print the accuracy of our model as a percentage of correct predictions based on the similarity threshold.

By using cosine similarity between embeddings, we can evaluate the model's performance in a way that accounts for the semantic correctness of the generated SQL queries, rather than relying solely on exact matches. This method provides a more flexible and accurate assessment of generative models.


In [ ]:
from tqdm import tqdm
from transformers import pipeline, BertTokenizer, BertModel
import torch
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

# Initialize BERT model and tokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained('bert-base-uncased')

def get_embedding(text):
    inputs = tokenizer(text, return_tensors='pt', truncation=True, padding=True)
    outputs = model(**inputs)
    return outputs.last_hidden_state.mean(dim=1)

def evaluate(sample):
    prompt = pipe.tokenizer.apply_chat_template(sample["messages"][:2], tokenize=False, add_generation_prompt=True)
    outputs = pipe(prompt, max_new_tokens=256, do_sample=True, temperature=0.7, top_k=50, top_p=0.95, eos_token_id=pipe.tokenizer.eos_token_id, pad_token_id=pipe.tokenizer.pad_token_id)
    predicted_answer = outputs[0]['generated_text'][len(prompt):].strip()

    predicted_embedding = get_embedding(predicted_answer).detach().numpy()
    reference_embedding = get_embedding(sample["messages"][2]["content"]).detach().numpy()

    similarity = cosine_similarity(predicted_embedding, reference_embedding)[0][0]

    # Define a threshold for considering answers as similar (e.g., 0.8)
    if similarity >= 0.8:
        return 1
    else:
        return 0

success_rate = []
number_of_eval_samples = 500

# Iterate over eval dataset and predict
for s in tqdm(eval_dataset.shuffle().select(range(number_of_eval_samples))):
    success_rate.append(evaluate(s))

# Compute accuracy
accuracy = sum(success_rate) / len(success_rate)

print(f"Accuracy: {accuracy*100:.2f}%")

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

  0%|          | 1/500 [00:03<30:59,  3.73s/it]/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(
  0%|          | 2/500 [00:09<42:15,  5.09s/it]/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(
  1%|          | 3/500 [00:14<40:38,  4.91s/it]/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(
  1%|          | 4/500 [00:20<43:14,  5.23s/it]/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximi

Accuracy: 99.00%


## 6. Deploy the model to Hugging Face space


Follow the next tutorials for this step:

* [HuggingFace formus](https://discuss.huggingface.co/)
* [HuggingFace tutorial about docker](https://huggingface.co/docs/hub/en/spaces-sdks-docker-first-demo)
* [HuggingFace tutorial about debugging](https://huggingface.co/learn/nlp-course/en/chapter8/2)
* [This video](https://www.youtube.com/watch?v=c10rsQkczu0&ab_channel=VenelinValkov)
* [Also this video](https://www.youtube.com/watch?v=QEaBAZQCtwE)

This tutorial was done with help from [this post](https://www.philschmid.de/fine-tune-llms-in-2024-with-trl).
